In [1]:
# Télécharger les ressources necéssaires pour utiliser le script
# !pip install python-binance

import os
import pandas as pd
from datetime import date, timedelta
from market_imbalance import MarketImbalance
from analysis_functions import find_imbalances_after_rise, find_imbalance_after_fall
from interact_with_binance import fetch_ohlcv
from binance.client import Client


In [2]:
# Récupérer les clés API à partir des variables d'environnement
api_key = os.environ.get('BINANCE_API_KEY')
api_secret = os.environ.get('BINANCE_API_SECRET')

# Initialiser le client Binance
client = Client(api_key, api_secret)

# Récupérer l'historique des prix pour une paire donnée depuis son listing sur la plateforme
df = fetch_ohlcv(client, symbol = "BTCUSDT", interval=Client.KLINE_INTERVAL_1HOUR, from_date= "1 Jan, 2015")
df

57752


timestamp            open            high             low  \
0     2017-08-17 04:00:00   4261.48000000   4313.62000000   4261.32000000   
1     2017-08-17 05:00:00   4308.83000000   4328.69000000   4291.37000000   
2     2017-08-17 06:00:00   4330.29000000   4345.45000000   4309.37000000   
3     2017-08-17 07:00:00   4316.62000000   4349.99000000   4287.41000000   
4     2017-08-17 08:00:00   4333.32000000   4377.85000000   4333.32000000   
...                   ...             ...             ...             ...   
57747 2024-03-24 15:00:00  65650.00000000  65750.07000000  65433.22000000   
57748 2024-03-24 16:00:00  65673.36000000  65838.88000000  65177.38000000   
57749 2024-03-24 17:00:00  65249.04000000  65539.01000000  64600.01000000   
57750 2024-03-24 18:00:00  65345.99000000  66045.99000000  65340.00000000   
57751 2024-03-24 19:00:00  65846.01000000  66041.67000000  65734.60000000   

                close         volume     close_time  quote_asset_volume  \
0       4308.83000000    47.18100900  1502945999999     202366.13839304   
1       4315.32000000    23.23491600  1502949599999     100304.82356749   
2       4324.35000000     7.22969100  1502953199999      31282.31266989   
3       4349.99000000     4.44324900  1502956799999      19241.05829986   
4       4360.69000000     0.97280700  1502960399999       4239.50358563   
...               ...            ...            ...                 ...   
57747  65673.36000000   856.48235000  1711295999999   56190409.98747650   
57748  65249.04000000  1202.84418000  1711299599999   78857363.80596330   
57749  65345.99000000  2260.69649000  1711303199999  147092471.06211470   
57750  65846.01000000  1923.39804000  1711306799999  126450342.56167010   
57751  65745.97000000   466.20877000  1711310399999   30718068.05096070   

       number_of_trades taker_buy_base_asset_volume  \
0                   171                 35.16050300   
1                   102                 21.44807100   
2                    36                  4.80286100   
3                    25                  2.60229200   
4                    28                  0.81465500   
...                 ...                         ...   
57747             61508                444.31861000   
57748             75123                495.26512000   
57749            125336               1066.27136000   
57750            100762               1050.17650000   
57751             19375                162.37131000   

      taker_buy_quote_asset_volume ignore  
0                  150952.47794304      0  
1                   92608.27972836      0  
2                   20795.31722405      0  
3                   11291.34701534      0  
4                    3552.74681715      0  
...                            ...    ...  
57747            29152142.91542450      0  
57748            32472176.77164700      0  
57749            69385361.46422450      0  
57750            69043170.92568340      0  
57751            10699612.54884850      0  

[57752 rows x 12 columns]

In [ ]:
# Création d'une instance de MarketImbalance
imbalance = MarketImbalance(
    timestamp='2024-03-20 10:00:00',  # Timestamp (as ID)
    open_price=100.0,
    close_price=110.0,
    delta_to_be_filled_in=10.0,
    is_full_filled=False,
    was_fullfilled_at=None,
    time_to_be_fullfilled=None,
    is_partially_filled=False,
    remaining_delta_open_price=None,
    remaining_delta_to_be_filled_in=None,
    candles_of_identification=['candle1', 'candle2'],
    candles_of_fullfilling=['candle3', 'candle4'],
    candles_of_partfilling=['candle5', 'candle6']
)

# Accès aux attributs de l'instance créée
print("Timestamp:", imbalance.timestamp)
print("Open Price:", imbalance.open_price)
print("Close Price:", imbalance.close_price)
# Et ainsi de suite pour les autres attributs


In [7]:
# (current_candle.name, price_difference, prev_candle.name, next_candle.name, [*prev_candle], [*current_candle], [*next_candle])
imbalances_after_rise = find_imbalances_after_rise(df)
for imbalance in imbalances_after_rise:
    for element in imbalance:
        print(element)

2017-08-17 08:00:00
10.010000000000218
2017-08-17 07:00:00
2017-08-17 09:00:00
[Timestamp('2017-08-17 07:00:00'), '4316.62000000', '4349.99000000', '4287.41000000', '4349.99000000', '4.44324900', 1502956799999, '19241.05829986', 25, '2.60229200', '11291.34701534', '0']
[Timestamp('2017-08-17 08:00:00'), '4333.32000000', '4377.85000000', '4333.32000000', '4360.69000000', '0.97280700', 1502960399999, '4239.50358563', 28, '0.81465500', '3552.74681715', '0']
[Timestamp('2017-08-17 09:00:00'), '4360.00000000', '4445.78000000', '4360.00000000', '4444.00000000', '10.76362300', 1502963999999, '47219.35594369', 43, '10.25840000', '44995.37815745', '0']
2017-08-17 09:00:00
21.960000000000036
2017-08-17 08:00:00
2017-08-17 10:00:00
[Timestamp('2017-08-17 08:00:00'), '4333.32000000', '4377.85000000', '4333.32000000', '4360.69000000', '0.97280700', 1502960399999, '4239.50358563', 28, '0.81465500', '3552.74681715', '0']
[Timestamp('2017-08-17 09:00:00'), '4360.00000000', '4445.78000000', '4360.00000

In [4]:
    
"""
    
    current_candle_name = rise[0][0]
    price_difference = rise[0][1]
    previous_candles_name = rise[0][2]
    next_candles_name = rise[0][3]
    previous_candles = rise[0][4]
    current_candles = rise[0][5]
    next_candles = rise[0][6]

print("current_candle_name : " + str(current_candle_name))
print("previous_candles_name : " + str(previous_candles_name))
print("next_candles_name : " + str(next_candles_name))
print("price_difference : " + str(price_difference))
print("previous_candles : " + str(previous_candles))
print("current_candles : " + str(current_candles))
print("next_candles : " + str(next_candles))"""

'\n    \n    current_candle_name = rise[0][0]\n    price_difference = rise[0][1]\n    previous_candles_name = rise[0][2]\n    next_candles_name = rise[0][3]\n    previous_candles = rise[0][4]\n    current_candles = rise[0][5]\n    next_candles = rise[0][6]\n\nprint("current_candle_name : " + str(current_candle_name))\nprint("previous_candles_name : " + str(previous_candles_name))\nprint("next_candles_name : " + str(next_candles_name))\nprint("price_difference : " + str(price_difference))\nprint("previous_candles : " + str(previous_candles))\nprint("current_candles : " + str(current_candles))\nprint("next_candles : " + str(next_candles))'

In [5]:
Imbalance_candles = pd.DataFrame([previous_candles, current_candles, next_candles], columns=['timestamp', 'open', 'high', 'low', 'close', 'volume', 'close_time', 'quote_asset_volume', 'number_of_trades', 'taker_buy_base_asset_volume', 'taker_buy_quote_asset_volume', 'ignore'])
Imbalance_candles

NameError: name 'previous_candles' is not defined

In [ ]:
# Identifier tous les imbalances

all_imbalances = find_imbalances_after_rise(df) + find_imbalance_after_fall(df)
print(len(all_imbalances))

# Return all imbalances
all_imbalances

9643


[(Timestamp('2017-08-17 08:00:00'),
  10.010000000000218,
  Timestamp('2017-08-17 07:00:00'),
  Timestamp('2017-08-17 09:00:00'),
  ['4316.62000000',
   '4349.99000000',
   '4287.41000000',
   '4349.99000000',
   '4.44324900',
   1502956799999,
   '19241.05829986',
   25,
   '2.60229200',
   '11291.34701534',
   '0'],
  ['4333.32000000',
   '4377.85000000',
   '4333.32000000',
   '4360.69000000',
   '0.97280700',
   1502960399999,
   '4239.50358563',
   28,
   '0.81465500',
   '3552.74681715',
   '0'],
  ['4360.00000000',
   '4445.78000000',
   '4360.00000000',
   '4444.00000000',
   '10.76362300',
   1502963999999,
   '47219.35594369',
   43,
   '10.25840000',
   '44995.37815745',
   '0']),
 (Timestamp('2017-08-17 09:00:00'),
  21.960000000000036,
  Timestamp('2017-08-17 08:00:00'),
  Timestamp('2017-08-17 10:00:00'),
  ['4333.32000000',
   '4377.85000000',
   '4333.32000000',
   '4360.69000000',
   '0.97280700',
   1502960399999,
   '4239.50358563',
   28,
   '0.81465500',
   '3552.7

In [ ]:
# retourne une liste des jours où il y a eu des imbalances
list_of_imbalance_start = []
for imbalance in all_imbalances :
    list_of_imbalance_start.append(imbalance[0])


In [ ]:
# retourne une liste des jours où il y a eu des imbalances qui n'ont pas été comblés par la suite
random_imbalance_after_a_rise = find_imbalances_after_rise(df)

df_exp = pd.DataFrame(random_imbalance_after_a_rise, columns=['timestamp', 'open', 'high', 'low', 'close', 'volume', 'close_time', 'quote_asset_volume', 'number_of_trades', 'taker_buy_base_asset_volume', 'taker_buy_quote_asset_volume', 'ignore'])
df_exp['timestamp'] = pd.to_datetime(df_exp['timestamp'], unit='ms')
df_exp.set_index('timestamp', inplace=True)

ValueError: 12 columns passed, passed data had 7 columns

In [ ]:
# un imbalance après une hausse est comblé si :
imbalance_timestamp = timestamp_imb
imbalance_open = n+1[low]
imbalance_close = n-1[high]
imbalance_depth = imbalance_open - imbalance_close
is_imbalance_filled = "function is_imbalance_filled_(imbalance, toutes les occurences dérrière)"

    """ pour chaque bougie après l'imbalance, regarder le prix le plus bas de la bougie. 
        si le prix le plus est égal ou inférieur à imbalance_close,
        alors is_imbalance_full_filled == true
        & imbalance_was_fullfilled_at = bougie[timestamp]
        
        si le prix le plus bas est strictement inférieur à imbalance_open
        is_imbalance_partially_filled == true
        
        
        mettre à jour la caractéristique de l'imbalance 
    """


In [ ]:
# code à modifier afin de pouvoir travailler avec tradingview sur des timeframes en heure et en minutes.
# Je suis limité à 5000 barres dans tradingview. Je dois donc réduire la liste des imbalances à ceux réalisés dans les 5000 derniers jours à partir d'aujourd'hui
# Get today's date
today = date.today()

# Calculate the date 5000 days ago
days_ago = today - timedelta(days=5000)
print(days_ago)

# Filter dates within the last 5000 days
recent_dates = [d for d in list_of_imbalance_start if d >= days_ago]

# Print recent dates
print("Recent dates within the last 5000 days:")
for d in recent_dates:
    print(d)